Install requirements

In [4]:
!pip install -r requirements.txt


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 8.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 67.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 54.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 94.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 731.7/731.7 MB 2.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.6/410.6 MB 3.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.6/121.6 MB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.5/56.5 MB 15.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.2/124.2 MB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 196.0/196.0 MB 2.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 166.0/166.0 MB 7.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.1/99.1 kB 16.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━

In [5]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier

import re
import string
import nltk

nltk.download('stopwords')
from nltk.stem.snowball import SnowballStemmer
stemmer = nltk.SnowballStemmer("english")

from nltk.corpus import stopwords
import string
stopword = set(stopwords.words("english"))

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Load your concatenated dataset

In [6]:
# Load the CSV data into a DataFrame
df = pd.read_csv('/content/concatenated_data.csv')

# Display the first few rows of the DataFrame
print(df.head())
df.shape

                                               tweet                    labels
0  rt mayasolovely woman shouldnt complain cleani...                  Not Hate
1  rt boy dats coldtyga dwn bad cuffin dat hoe place  Offensive or Hate Speech
2  rt urkindofbrand dawg rt ever fuck bitch start...  Offensive or Hate Speech
3           rt cganderson vivabased look like tranny  Offensive or Hate Speech
4  rt shenikaroberts shit hear might true might f...  Offensive or Hate Speech


(242738, 2)

In [7]:
# Assuming combined_df is your full dataset
reduced_df = df.sample(n=100000, random_state=42)  # Randomly select 100,000 rows
print(reduced_df.shape)

# Proceed with your preprocessing on the reduced dataset
x = np.array(reduced_df["tweet"])
y = np.array(reduced_df["labels"])


(100000, 2)


In [8]:
def clean(text):
    text = str(text).lower()
    text = re.sub('\[.*?\]', '', text)
    text = re.sub('https?://\S+|www\.\S+', '', text)
    text = re.sub('<.*?>+', '', text)
    text = re.sub('[%s]' % re.escape(string.punctuation), '', text)
    text = re.sub('\n', '', text)
    text = re.sub('\w*\d\w*', "", text)
    text = [word for word in text.split() if word not in stopword]
    text = " ".join(text)
    return text
# Apply cleaning function to the 'tweet' column of both dataframes
reduced_df['tweet'] = reduced_df['tweet'].apply(clean)
texts = reduced_df["tweet"].tolist()

In [9]:
from sklearn.feature_extraction.text import TfidfVectorizer

# Initialize a TF-IDF Vectorizer
tfidf_vectorizer = TfidfVectorizer(max_features=100000)  # Adjust the number of features as necessary

# Fit and transform the tweets to create a matrix of TF-IDF features
tfidf_matrix = tfidf_vectorizer.fit_transform(reduced_df)

Load the RoBERTa Model and Tokenizer

In [10]:
# Load model directly
from transformers import AutoModelForSequenceClassification, AutoTokenizer

# Load the tokenizer and model
model_name = "facebook/roberta-hate-speech-dynabench-r4-target"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForSequenceClassification.from_pretrained(model_name)
model.eval()

tokenizer_config.json:   0%|          | 0.00/1.11k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/816 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/499M [00:00<?, ?B/s]

RobertaForSequenceClassification(
  (roberta): RobertaModel(
    (embeddings): RobertaEmbeddings(
      (word_embeddings): Embedding(50265, 768, padding_idx=1)
      (position_embeddings): Embedding(514, 768, padding_idx=1)
      (token_type_embeddings): Embedding(1, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): RobertaEncoder(
      (layer): ModuleList(
        (0-11): 12 x RobertaLayer(
          (attention): RobertaAttention(
            (self): RobertaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): RobertaSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
             

Tokenizing texts

In [ ]:
import torch
from torch.nn.functional import softmax

# Tokenize and predict in batches to manage memory
def predict_hf_model(texts, tokenizer, model, batch_size=100):
    predictions = []
    for i in range(0, len(texts), batch_size):
        batch_texts = texts[i:i+batch_size]
        encoding = tokenizer(batch_texts, padding=True, truncation=True, return_tensors="pt")

        with torch.no_grad():
            outputs = model(**encoding)
            batch_predictions = softmax(outputs.logits, dim=1)
            predictions.extend(batch_predictions.argmax(dim=1).cpu().numpy())

    return predictions

# Generate predictions with Hugging Face model
roberta_predictions = predict_hf_model(texts, tokenizer, model)

Make Predictions

In [ ]:
sample_text = "I don't like him"
print(ensemble_predict(sample_text))
